# 0. Libraries

In [1]:
import os
import pickle
import warnings

import pandas as pd
import numpy  as np

from utils                   import *
from sklearn.model_selection import train_test_split
from sklearn.preprocessing   import StandardScaler, LabelEncoder, OneHotEncoder
from sklearn.exceptions      import ConvergenceWarning

warnings.filterwarnings("ignore", category=ConvergenceWarning)

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

## 0.1. Settings parameters

### 0.1.1. Seed

In [2]:
# seed
seed = 42

### 0.1.2. Paths

In [3]:
# gets the current working directory (where the notebook is located)
actual_path = os.getcwd()

# gets the current working root directory
root_path = os.path.abspath(os.path.join(actual_path, "..", ".."))

# gets the parent directory (one level up)
parent_path = os.path.dirname(actual_path)

# extract folder name from parent directory
parent_folder_name = os.path.basename(parent_path)

print(f"Parent path name: {parent_folder_name}")

Parent path name: PROJECT_17


## 0.2. Removing old files 

In [65]:
# set the directories to analyze
path_csv = f'{root_path}/{parent_folder_name}/DATAS/GOLD'
path_pkl = f'{root_path}/{parent_folder_name}/PKL'

for path in [path_csv, path_pkl]:
    # list all files in the directory
    files = os.listdir(path_csv)

    print('Removing files\n')

    # iterates over the files and deletes those that do not have the parent folder name at the end
    for file in files:
        if not file.endswith(f"_{parent_folder_name}.{path[5::]}"):
            caminho_arquivo = os.path.join(path, file)
            os.remove(caminho_arquivo)
            print(f"File {file} removed.")

    print("\nOperation completed.\n")

Removing files

File abt_submission_PROJECT_17.csv removed.
File abt_train_00_PROJECT_17.csv removed.
File abt_test_00_PROJECT_17.csv removed.
File abt_test_01_PROJECT_17.csv removed.
File abt_train_01_PROJECT_17.csv removed.

Operation completed.

Removing files


Operation completed.



# 1. Data

In [5]:
### AVALIAR O USO DESSA FUNÇÃO PARA REDUZIR A MEMÓRIA UTILIZADA ###

# def rm(df):
#     start_mem = df.memory_usage().sum() / 1024**2
#     print('Memory usage of dataframe is {:.2f} MB'.format(start_mem))    
#     for col in df.columns:
#         col_type = df[col].dtype        
#         if col_type != object:
#             c_min = df[col].min()
#             c_max = df[col].max()
#             if str(col_type)[:3] == 'int':
#                 if c_min > np.iinfo(np.int8).min and c_max < np.iinfo(np.int8).max:
#                     df[col] = df[col].astype(np.int8)
#                 elif c_min > np.iinfo(np.int16).min and c_max < np.iinfo(np.int16).max:
#                     df[col] = df[col].astype(np.int16)
#                 elif c_min > np.iinfo(np.int32).min and c_max < np.iinfo(np.int32).max:
#                     df[col] = df[col].astype(np.int32)
#                 elif c_min > np.iinfo(np.int64).min and c_max < np.iinfo(np.int64).max:
#                     df[col] = df[col].astype(np.int64)  
#             else:
#                 if c_min > np.finfo(np.float16).min and c_max < np.finfo(np.float16).max:
#                     df[col] = df[col].astype(np.float16)
#                 elif c_min > np.finfo(np.float32).min and c_max < np.finfo(np.float32).max:
#                     df[col] = df[col].astype(np.float32)
#                 else:
#                     df[col] = df[col].astype(np.float64)
#         else:
#             df[col] = df[col].astype('category')

#     end_mem = df.memory_usage().sum() / 1024**2
#     print('Memory usage after optimization is: {:.2f} MB'.format(end_mem))
#     print('Decreased by {:.1f}%'.format(100 * (start_mem - end_mem) / start_mem))
    
#     return df

# # loading
# data_train_00 = rm(pd.read_csv(f'{root_path}/DADOS/application_train_merged_bureau.csv'))

# #
# ncol = data_train_00.columns

# # # checking
# # data_train_00.head()

In [6]:
# loading
data_train_00 = pd.read_csv(f'{root_path}/DADOS/application_train_merged_bureau.csv')

# checking
data_train_00.head()

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
0      247330       0         Cash loans           F            N   
1      425716       1         Cash loans           F            Y   
2      331625       0         Cash loans           M            Y   
3      455397       0    Revolving loans           F            N   
4      449114       0         Cash loans           F            N   

  FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
0               N             0          157500.0    706410.0      67072.5   
1               Y             1          121500.0    545040.0      25407.0   
2               Y             1          225000.0    942300.0      27679.5   
3               Y             2          144000.0    180000.0       9000.0   
4               Y             0          112500.0    729792.0      37390.5   

   AMT_GOODS_PRICE NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
0         679500.0   Unaccompanied  Commercial associate   
1         450000.0   Unaccompanied               Working   
2         675000.0   Unaccompanied               Working   
3         180000.0   Unaccompanied  Commercial associate   
4         630000.0   Unaccompanied             Pensioner   

             NAME_EDUCATION_TYPE NAME_FAMILY_STATUS    NAME_HOUSING_TYPE  \
0               Higher education            Married    House / apartment   
1  Secondary / secondary special            Married    House / apartment   
2  Secondary / secondary special            Married  Municipal apartment   
3  Secondary / secondary special          Separated    House / apartment   
4  Secondary / secondary special     Civil marriage    House / apartment   

   REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  DAYS_REGISTRATION  \
0                    0.032561      -14653          -2062            -8599.0   
1                    0.007114      -13995          -2246             -348.0   
2                    0.022625      -21687          -1335            -6306.0   
3                    0.006629      -13071          -2292             -742.0   
4                    0.046220      -19666         365243             -169.0   

   DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  FLAG_EMP_PHONE  FLAG_WORK_PHONE  \
0            -2087          NaN           1               1                0   
1             -172         12.0           1               1                1   
2            -4026          1.0           1               1                0   
3            -1201          NaN           1               1                1   
4            -3112          NaN           1               0                0   

   FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL        OCCUPATION_TYPE  \
0                 1           1           0  Private service staff   
1                 1           1           0            Secretaries   
2                 1           0           0               Laborers   
3                 1           1           0          Cooking staff   
4                 1           0           0                    NaN   

   CNT_FAM_MEMBERS  REGION_RATING_CLIENT  REGION_RATING_CLIENT_W_CITY  \
0              2.0                     1                            1   
1              3.0                     2                            2   
2              3.0                     2                            2   
3              3.0                     2                            2   
4              2.0                     1                            1   

  WEEKDAY_APPR_PROCESS_START  HOUR_APPR_PROCESS_START  \
0                  WEDNESDAY                       13   
1                     MONDAY                       10   
2                   THURSDAY                       10   
3                     MONDAY                        8   
4                     FRIDAY                       10   

   REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
0                           0                           0   
1                   

## 1.1. Data Filtering

In [7]:
# dropping sensible variables
data_train_00 = data_train_00.drop(columns='CODE_GENDER')

# is required to drop lines where 'NAME_FAMILY_STATUS' is equals to 'Unknown' because there is only one in the entire database
data_train_00 = data_train_00[data_train_00['NAME_FAMILY_STATUS'] != 'Unknown']

## 1.2. Feature Engineering

In [10]:
# feature engineering
data_train_00 = generate_feature_engineering(data_train_00)

# checking
data_train_00.head()

# 1.3. Holdout

In [12]:
# holdout in train and test
data_train_01, data_test_01 = train_test_split(data_train_00, test_size=0.3, random_state=seed)

In [13]:
# checking
data_train_01.head()

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE FLAG_OWN_CAR FLAG_OWN_REALTY  \
78719      404124       0         Cash loans            N               Y   
2004       283810       0         Cash loans            Y               Y   
33911      114564       1         Cash loans            N               Y   
6280       415891       0    Revolving loans            N               N   
55616      353829       0    Revolving loans            Y               Y   

       CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
78719             0           68850.0    521280.0      22216.5   
2004              0          135000.0    168102.0      16753.5   
33911             1           90000.0    566055.0      22063.5   
6280              0          180000.0    270000.0      13500.0   
55616             0          135000.0    202500.0      10125.0   

       AMT_GOODS_PRICE NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
78719         450000.0   Unaccompanied             Pensioner   
2004          148500.0   Unaccompanied  Commercial associate   
33911         472500.0   Unaccompanied  Commercial associate   
6280          270000.0   Unaccompanied  Commercial associate   
55616         202500.0   Unaccompanied               Working   

                 NAME_EDUCATION_TYPE NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
78719  Secondary / secondary special              Widow  House / apartment   
2004   Secondary / secondary special            Married  House / apartment   
33911  Secondary / secondary special            Married  House / apartment   
6280                Higher education            Married       With parents   
55616               Higher education            Married  House / apartment   

       REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
78719                    0.019689      -22863         365243   
2004                     0.035792      -16269           -612   
33911                    0.005144      -12073           -659   
6280                     0.035792      -12327          -2713   
55616                    0.008230      -12559           -762   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
78719            -4162.0            -4294          NaN           1   
2004             -8821.0            -4693         10.0           1   
33911            -2917.0             -316          NaN           1   
6280             -5987.0            -4222          NaN           1   
55616             -912.0            -3019          4.0           1   

       FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
78719               0                0                 1           0   
2004                1                0                 1           0   
33911               1                0                 1           0   
6280                1                0                 1           0   
55616               1                0                 1           0   

       FLAG_EMAIL OCCUPATION_TYPE  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
78719           0             NaN              1.0                     2   
2004            0        Laborers              2.0                     2   
33911           0  Cleaning staff              3.0                     2   
6280            0         Drivers              2.0                     2   
55616           0  Cleaning staff              2.0                     2   

       REGION_RATING_CLIENT_W_CITY WEEKDAY_APPR_PROCESS_START  \
78719                            2                     FRIDAY   
2004                             2                     FRIDAY   
33911                            2                   SATURDAY   
6280                             2                     FRIDAY   
55616                            2                     FRIDAY   

       HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
78719                       16                           0   
2004                        10                           0   
33911               

In [14]:
# checking
data_test_01.head()

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE FLAG_OWN_CAR FLAG_OWN_REALTY  \
55944      189821       0         Cash loans            N               N   
48387      292112       0         Cash loans            Y               Y   
1389       409929       0         Cash loans            N               Y   
68844      361285       0    Revolving loans            Y               Y   
14458      232524       0         Cash loans            N               N   

       CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
55944             1           81000.0    254700.0      20250.0   
48387             1          148500.0    545040.0      25537.5   
1389              0          157500.0   1006920.0      42790.5   
68844             1          630000.0    225000.0      11250.0   
14458             0          112500.0    573628.5      22878.0   

       AMT_GOODS_PRICE NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
55944         225000.0   Unaccompanied               Working   
48387         450000.0   Unaccompanied               Working   
1389          900000.0   Unaccompanied             Pensioner   
68844         225000.0   Unaccompanied  Commercial associate   
14458         463500.0   Unaccompanied               Working   

                 NAME_EDUCATION_TYPE NAME_FAMILY_STATUS    NAME_HOUSING_TYPE  \
55944  Secondary / secondary special            Married    House / apartment   
48387  Secondary / secondary special            Married    House / apartment   
1389   Secondary / secondary special            Married  Municipal apartment   
68844               Higher education            Married    House / apartment   
14458  Secondary / secondary special            Married    House / apartment   

       REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
55944                    0.010006      -14380          -3828   
48387                    0.009657      -15920          -2771   
1389                     0.005002      -22116         365243   
68844                    0.008474      -14308          -5267   
14458                    0.031329      -19427          -5248   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
55944            -2709.0            -4302          NaN           1   
48387            -3271.0            -4015         16.0           1   
1389            -13359.0            -4042          NaN           1   
68844            -1902.0            -4743          5.0           1   
14458           -11827.0            -2264          NaN           1   

       FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
55944               1                0                 1           0   
48387               1                0                 1           0   
1389                0                0                 1           0   
68844               1                0                 1           0   
14458               1                0                 1           0   

       FLAG_EMAIL OCCUPATION_TYPE  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
55944           0      Core staff              3.0                     2   
48387           0         Drivers              3.0                     2   
1389            0             NaN              2.0                     3   
68844           0        Managers              3.0                     2   
14458           0     Sales staff              2.0                     2   

       REGION_RATING_CLIENT_W_CITY WEEKDAY_APPR_PROCESS_START  \
55944                            2                     FRIDAY   
48387                            2                     SUNDAY   
1389                             3                     FRIDAY   
68844                            2                     MONDAY   
14458                            2                   SATURDAY   

       HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
55944                       10                           0   
48387                       11                           0   
1389    

In [15]:
# cleaning memory
del data_train_00

# 2. Analytics

In [16]:
# backup
data_train_02 = data_train_01.copy()

# checking
data_train_02.head()

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE FLAG_OWN_CAR FLAG_OWN_REALTY  \
78719      404124       0         Cash loans            N               Y   
2004       283810       0         Cash loans            Y               Y   
33911      114564       1         Cash loans            N               Y   
6280       415891       0    Revolving loans            N               N   
55616      353829       0    Revolving loans            Y               Y   

       CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
78719             0           68850.0    521280.0      22216.5   
2004              0          135000.0    168102.0      16753.5   
33911             1           90000.0    566055.0      22063.5   
6280              0          180000.0    270000.0      13500.0   
55616             0          135000.0    202500.0      10125.0   

       AMT_GOODS_PRICE NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
78719         450000.0   Unaccompanied             Pensioner   
2004          148500.0   Unaccompanied  Commercial associate   
33911         472500.0   Unaccompanied  Commercial associate   
6280          270000.0   Unaccompanied  Commercial associate   
55616         202500.0   Unaccompanied               Working   

                 NAME_EDUCATION_TYPE NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
78719  Secondary / secondary special              Widow  House / apartment   
2004   Secondary / secondary special            Married  House / apartment   
33911  Secondary / secondary special            Married  House / apartment   
6280                Higher education            Married       With parents   
55616               Higher education            Married  House / apartment   

       REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
78719                    0.019689      -22863         365243   
2004                     0.035792      -16269           -612   
33911                    0.005144      -12073           -659   
6280                     0.035792      -12327          -2713   
55616                    0.008230      -12559           -762   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
78719            -4162.0            -4294          NaN           1   
2004             -8821.0            -4693         10.0           1   
33911            -2917.0             -316          NaN           1   
6280             -5987.0            -4222          NaN           1   
55616             -912.0            -3019          4.0           1   

       FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
78719               0                0                 1           0   
2004                1                0                 1           0   
33911               1                0                 1           0   
6280                1                0                 1           0   
55616               1                0                 1           0   

       FLAG_EMAIL OCCUPATION_TYPE  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
78719           0             NaN              1.0                     2   
2004            0        Laborers              2.0                     2   
33911           0  Cleaning staff              3.0                     2   
6280            0         Drivers              2.0                     2   
55616           0  Cleaning staff              2.0                     2   

       REGION_RATING_CLIENT_W_CITY WEEKDAY_APPR_PROCESS_START  \
78719                            2                     FRIDAY   
2004                             2                     FRIDAY   
33911                            2                   SATURDAY   
6280                             2                     FRIDAY   
55616                            2                     FRIDAY   

       HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
78719                       16                           0   
2004                        10                           0   
33911               

In [17]:
# # cleaning memory
# del data_train_01

## 2.1. Metadata

In [18]:
# metadata
metadata = generate_metadata(data_train_02, 'TARGET')

# checking
metadata.head()

FEATURE         USE  CARDINALITY  \
0                   SK_ID_CURR  explicable        56378   
1      HOUR_APPR_PROCESS_START  explicable           24   
2   REG_REGION_NOT_LIVE_REGION  explicable            2   
3   REG_REGION_NOT_WORK_REGION  explicable            2   
4  LIVE_REGION_NOT_WORK_REGION  explicable            2   

                                         UNIQUE_DATA  VL_NULL  PC_NULL   TYPE  
0  [404124, 283810, 114564, 415891, 353829, 21246...        0      0.0  int64  
1  [16, 10, 14, 13, 15, 6, 8, 9, 12, 11, 17, 18, ...        0      0.0  int64  
2                                             [0, 1]        0      0.0  int64  
3                                             [0, 1]        0      0.0  int64  
4                                             [0, 1]        0      0.0  int64

## 2.2. Dimensions

In [19]:
# dimensions train
print(f'Rows:    {data_train_02.shape[0]}')
print(f'Columns: {data_train_02.shape[1]}')

Rows:    56378
Columns: 1605


# 3. Drop

In [20]:
# backup
data_train_03 = data_train_02.copy()

# checking
data_train_03.head()

SK_ID_CURR  TARGET NAME_CONTRACT_TYPE FLAG_OWN_CAR FLAG_OWN_REALTY  \
78719      404124       0         Cash loans            N               Y   
2004       283810       0         Cash loans            Y               Y   
33911      114564       1         Cash loans            N               Y   
6280       415891       0    Revolving loans            N               N   
55616      353829       0    Revolving loans            Y               Y   

       CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
78719             0           68850.0    521280.0      22216.5   
2004              0          135000.0    168102.0      16753.5   
33911             1           90000.0    566055.0      22063.5   
6280              0          180000.0    270000.0      13500.0   
55616             0          135000.0    202500.0      10125.0   

       AMT_GOODS_PRICE NAME_TYPE_SUITE      NAME_INCOME_TYPE  \
78719         450000.0   Unaccompanied             Pensioner   
2004          148500.0   Unaccompanied  Commercial associate   
33911         472500.0   Unaccompanied  Commercial associate   
6280          270000.0   Unaccompanied  Commercial associate   
55616         202500.0   Unaccompanied               Working   

                 NAME_EDUCATION_TYPE NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
78719  Secondary / secondary special              Widow  House / apartment   
2004   Secondary / secondary special            Married  House / apartment   
33911  Secondary / secondary special            Married  House / apartment   
6280                Higher education            Married       With parents   
55616               Higher education            Married  House / apartment   

       REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
78719                    0.019689      -22863         365243   
2004                     0.035792      -16269           -612   
33911                    0.005144      -12073           -659   
6280                     0.035792      -12327          -2713   
55616                    0.008230      -12559           -762   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
78719            -4162.0            -4294          NaN           1   
2004             -8821.0            -4693         10.0           1   
33911            -2917.0             -316          NaN           1   
6280             -5987.0            -4222          NaN           1   
55616             -912.0            -3019          4.0           1   

       FLAG_EMP_PHONE  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  \
78719               0                0                 1           0   
2004                1                0                 1           0   
33911               1                0                 1           0   
6280                1                0                 1           0   
55616               1                0                 1           0   

       FLAG_EMAIL OCCUPATION_TYPE  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
78719           0             NaN              1.0                     2   
2004            0        Laborers              2.0                     2   
33911           0  Cleaning staff              3.0                     2   
6280            0         Drivers              2.0                     2   
55616           0  Cleaning staff              2.0                     2   

       REGION_RATING_CLIENT_W_CITY WEEKDAY_APPR_PROCESS_START  \
78719                            2                     FRIDAY   
2004                             2                     FRIDAY   
33911                            2                   SATURDAY   
6280                             2                     FRIDAY   
55616                            2                     FRIDAY   

       HOUR_APPR_PROCESS_START  REG_REGION_NOT_LIVE_REGION  \
78719                       16                           0   
2004                        10                           0   
33911               

In [21]:
# cleaning memory
del data_train_02

## 3.1. Drop First

In [28]:
# list variables to drop first
list_variables_to_drop = ['SK_ID_CURR', 'TARGET']

# printing
print('List of variables to drop:\n', list_variables_to_drop)
print('Len of list of variables to drop:', len(list_variables_to_drop))

List of variables to drop:
 ['SK_ID_CURR', 'TARGET']
Len of list of variables to drop: 2


In [23]:
# dropping
data_train_03 = data_train_03.drop(columns=list_variables_to_drop)

In [24]:
# saving pkl
with open(f'{root_path}/{parent_folder_name}/PKL/prd_list_variables_to_drop_{parent_folder_name}.pkl', 'wb') as file:
    pickle.dump(list_variables_to_drop, file)

## 3.2. Drop NaN

In [27]:
# cutoff nan
cutoff_missing = 70

# list variables to drop nan
list_variables_to_drop_nan = metadata[metadata.PC_NULL >= cutoff_missing].FEATURE.tolist()

# printing
print('List of variables to drop nan:\n', list_variables_to_drop_nan)
print('Len of list of variables to drop nan:', len(list_variables_to_drop_nan))

List of variables to drop nan:
 ['AVG_STATUS_1_MAX_BB_BB', 'SUM_STATUS_1_MAX_BB_BB', 'SUM_STATUS_0_MAX_BB_BB', 'SUM_STATUS_X_MIN_BB_BB', 'SUM_STATUS_C_MIN_BB_BB', 'SUM_STATUS_5_MIN_BB_BB', 'SUM_STATUS_4_MIN_BB_BB', 'SUM_STATUS_3_MIN_BB_BB', 'SUM_STATUS_2_MIN_BB_BB', 'SUM_STATUS_1_MIN_BB_BB', 'SUM_STATUS_2_MAX_BB_BB', 'SUM_STATUS_0_MIN_BB_BB', 'SUM_STATUS_C_AVG_BB_BB', 'SUM_STATUS_5_AVG_BB_BB', 'SUM_STATUS_4_AVG_BB_BB', 'SUM_STATUS_3_AVG_BB_BB', 'SUM_STATUS_2_AVG_BB_BB', 'SUM_STATUS_1_AVG_BB_BB', 'SUM_STATUS_0_AVG_BB_BB', 'SUM_STATUS_X_SUM_BB_BB', 'SUM_STATUS_C_SUM_BB_BB', 'SUM_STATUS_X_AVG_BB_BB', 'SUM_STATUS_3_MAX_BB_BB', 'SUM_STATUS_4_MAX_BB_BB', 'SUM_STATUS_5_MAX_BB_BB', 'MIN_STATUS_X_AVG_BB_BB', 'MIN_STATUS_C_AVG_BB_BB', 'MIN_STATUS_5_AVG_BB_BB', 'MIN_STATUS_4_AVG_BB_BB', 'MIN_STATUS_3_AVG_BB_BB', 'MIN_STATUS_2_AVG_BB_BB', 'MIN_STATUS_1_AVG_BB_BB', 'MIN_STATUS_0_AVG_BB_BB', 'MIN_STATUS_X_SUM_BB_BB', 'MIN_STATUS_C_SUM_BB_BB', 'MIN_STATUS_5_SUM_BB_BB', 'MIN_STATUS_4_SUM_BB_BB', 'MIN_

In [29]:
# dropping
data_train_03 = data_train_03.drop(columns=list_variables_to_drop_nan)

In [30]:
# saving pkl
with open(f'{root_path}/{parent_folder_name}/PKL/prd_list_variables_to_drop_nan_{parent_folder_name}.pkl', 'wb') as file:
    pickle.dump(list_variables_to_drop_nan, file)

# 4. Transformation

In [31]:
# backup
data_train_04 = data_train_03.copy()

# checking
data_train_04.head()

NAME_CONTRACT_TYPE FLAG_OWN_CAR FLAG_OWN_REALTY  CNT_CHILDREN  \
78719         Cash loans            N               Y             0   
2004          Cash loans            Y               Y             0   
33911         Cash loans            N               Y             1   
6280     Revolving loans            N               N             0   
55616    Revolving loans            Y               Y             0   

       AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  AMT_GOODS_PRICE  \
78719           68850.0    521280.0      22216.5         450000.0   
2004           135000.0    168102.0      16753.5         148500.0   
33911           90000.0    566055.0      22063.5         472500.0   
6280           180000.0    270000.0      13500.0         270000.0   
55616          135000.0    202500.0      10125.0         202500.0   

      NAME_TYPE_SUITE      NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
78719   Unaccompanied             Pensioner  Secondary / secondary special   
2004    Unaccompanied  Commercial associate  Secondary / secondary special   
33911   Unaccompanied  Commercial associate  Secondary / secondary special   
6280    Unaccompanied  Commercial associate               Higher education   
55616   Unaccompanied               Working               Higher education   

      NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  REGION_POPULATION_RELATIVE  \
78719              Widow  House / apartment                    0.019689   
2004             Married  House / apartment                    0.035792   
33911            Married  House / apartment                    0.005144   
6280             Married       With parents                    0.035792   
55616            Married  House / apartment                    0.008230   

       DAYS_BIRTH  DAYS_EMPLOYED  DAYS_REGISTRATION  DAYS_ID_PUBLISH  \
78719      -22863         365243            -4162.0            -4294   
2004       -16269           -612            -8821.0            -4693   
33911      -12073           -659            -2917.0             -316   
6280       -12327          -2713            -5987.0            -4222   
55616      -12559           -762             -912.0            -3019   

       OWN_CAR_AGE  FLAG_MOBIL  FLAG_EMP_PHONE  FLAG_WORK_PHONE  \
78719          NaN           1               0                0   
2004          10.0           1               1                0   
33911          NaN           1               1                0   
6280           NaN           1               1                0   
55616          4.0           1               1                0   

       FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL OCCUPATION_TYPE  \
78719                 1           0           0             NaN   
2004                  1           0           0        Laborers   
33911                 1           0           0  Cleaning staff   
6280                  1           0           0         Drivers   
55616                 1           0           0  Cleaning staff   

       CNT_FAM_MEMBERS  REGION_RATING_CLIENT  REGION_RATING_CLIENT_W_CITY  \
78719              1.0                     2                            2   
2004               2.0                     2                            2   
33911              3.0                     2                            2   
6280               2.0                     2                            2   
55616              2.0                     2                            2   

      WEEKDAY_APPR_PROCESS_START  HOUR_APPR_PROCESS_START  \
78719                     FRIDAY                       16   
2004                      FRIDAY                       10   
33911                   SATURDAY                       14   
6280                      FRIDAY                       13   
55616                     FRIDAY                       15   

       REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
78719                           0                           0   
2004                            0            

In [32]:
# cleaning memory
del data_train_03

## 4.1. Filling NaN

In [33]:
# creating dictionnaire to fill nan
dict_to_fillna = {}

### 4.1.1 Categorical Columns

In [34]:
# categorical columns
categorical_columns = data_train_04.select_dtypes(include=['object']).columns

for column in categorical_columns:
    dict_to_fillna[column] = 'VERIFY'
    
    data_train_04[column] = data_train_04[column].fillna('VERIFY')

### 4.1.2. Numerical Columns

In [35]:
# creating dict to fillna (numerical)
numerical_columns = data_train_04.select_dtypes(include=['float64', 'float32', 'float16', 'int64', 'int32', 'int16', 'int8'], exclude=['object']).columns

for column in numerical_columns:
    dict_to_fillna[column] = data_train_04[column].mean()

    data_train_04[column] = data_train_04[column].fillna(data_train_04[column].mean())

In [36]:
# saving pkl
with open(f'{root_path}/{parent_folder_name}/PKL/prd_dict_to_fillna_{parent_folder_name}.pkl', 'wb') as file:
    pickle.dump(dict_to_fillna, file)

## 4.2. Encoding

In [37]:
# cutoff cardinality
cutoff_cardinality = 10

### 4.2.1. Label Encoder

In [39]:
# list variables to label encoder
list_variables_to_label_encoder = metadata[(metadata['CARDINALITY'] >= cutoff_cardinality) & (metadata['TYPE'] == 'object') & (metadata['USE'] != 'TARGET')].FEATURE.tolist()

# printing
print('List variables to Label Encoder:\n', list_variables_to_label_encoder)
print('Len of list variables to Label Encoder:', len(list_variables_to_label_encoder))

List variables to Label Encoder:
 ['ORGANIZATION_TYPE', 'OCCUPATION_TYPE']
Len of list variables to Label Encoder: 2


In [40]:
# removing variables to drop from list of variables to label encoder
for item in list_variables_to_drop + list_variables_to_drop_nan:
    if item in list_variables_to_label_encoder:
        list_variables_to_label_encoder.remove(item)

In [41]:
# creating dict
encoders = {}

# loop for
for column in list_variables_to_label_encoder:
    encoder = LabelEncoder()
    data_train_04[column] = encoder.fit_transform(data_train_04[column])

    # Armazena o encoder para a coluna atual em um dicionário
    encoders[column] = encoder

# creating data to label encoder
dict_to_label_encoder = {
    'encoders': encoders,
    'columns': list_variables_to_label_encoder
}

In [42]:
# saving pkl
with open(f'{root_path}/{parent_folder_name}/PKL/prd_dict_to_label_encoder_{parent_folder_name}.pkl', 'wb') as file:
    pickle.dump(dict_to_label_encoder, file)

### 4.2.2. One Hot Encoder

In [44]:
# list variables to one hot encoder
list_variables_to_one_hot_encoder = metadata[(metadata['CARDINALITY'] <= cutoff_cardinality) & (metadata['TYPE'] == 'object') & (metadata['USE'] != 'TARGET')].FEATURE.tolist()

# printing
print('List variables to One Hot Encoder:\n', list_variables_to_one_hot_encoder)
print('Len of list variables to One Hot Encoder:', len(list_variables_to_one_hot_encoder))

List variables to One Hot Encoder:
 ['NAME_CONTRACT_TYPE', 'FLAG_OWN_CAR', 'FLAG_OWN_REALTY', 'FONDKAPREMONT_MODE', 'NAME_TYPE_SUITE', 'NAME_FAMILY_STATUS', 'NAME_EDUCATION_TYPE', 'NAME_HOUSING_TYPE', 'HOUSETYPE_MODE', 'WALLSMATERIAL_MODE', 'EMERGENCYSTATE_MODE', 'WEEKDAY_APPR_PROCESS_START', 'NAME_INCOME_TYPE']
Len of list variables to One Hot Encoder: 13


In [45]:
# removing variables to drop from list of variables to one hot encoder
for item in list_variables_to_drop + list_variables_to_drop_nan:
    if item in list_variables_to_one_hot_encoder:
        list_variables_to_one_hot_encoder.remove(item)

In [46]:
# condition
if len(list_variables_to_one_hot_encoder) > 0:
    # Instanciando o encoder
    encoder = OneHotEncoder(drop='first', sparse_output=False, handle_unknown='ignore')

    # Aplicando o one-hot encoding
    encoded_data = encoder.fit_transform(data_train_04[list_variables_to_one_hot_encoder])
    encoded_cols = encoder.get_feature_names_out(list_variables_to_one_hot_encoder)

    data_encoded = pd.DataFrame(encoded_data, columns=encoded_cols, index=data_train_04.index)

    data_train_04 = pd.concat([data_train_04.drop(list_variables_to_one_hot_encoder, axis=1), data_encoded], axis=1)

    # Salva o encoder e a lista de colunas em um file .pkl
    dict_to_one_hot_encoder = {
        'encoder': encoder,
        'columns': list_variables_to_one_hot_encoder
    }
else:
    # Salva o encoder e a lista de colunas em um file .pkl
    dict_to_one_hot_encoder = {
        'encoder': [],
        'columns': []
    }

In [47]:
# saving pkl
with open(f'{root_path}/{parent_folder_name}/PKL/prd_dict_to_one_hot_encoder_{parent_folder_name}.pkl', 'wb') as file:
    pickle.dump(dict_to_one_hot_encoder, file)

## 4.3. Correlations

In [48]:
# Obtém a lista de variáveis para manter (não remover)
list_of_variables_to_keep_low_correlation = keep_low_correlation_variables(data_train_04.sample(50000, random_state=seed))

print('List of variables to keep - low correlation:\n', list_of_variables_to_keep_low_correlation)
print('Len of list variables to keep - low correlation:', len(list_of_variables_to_keep_low_correlation))

List of variables to keep - low correlation:
  ['CNT_CHILDREN', 'AMT_INCOME_TOTAL', 'AMT_CREDIT', 'AMT_ANNUITY', 'REGION_POPULATION_RELATIVE', 'DAYS_BIRTH', 'DAYS_EMPLOYED', 'DAYS_REGISTRATION', 'DAYS_ID_PUBLISH', 'OWN_CAR_AGE', 'FLAG_MOBIL', 'FLAG_WORK_PHONE', 'FLAG_CONT_MOBILE', 'FLAG_PHONE', 'FLAG_EMAIL', 'OCCUPATION_TYPE', 'REGION_RATING_CLIENT', 'HOUR_APPR_PROCESS_START', 'REG_REGION_NOT_LIVE_REGION', 'REG_REGION_NOT_WORK_REGION', 'REG_CITY_NOT_LIVE_CITY', 'REG_CITY_NOT_WORK_CITY', 'ORGANIZATION_TYPE', 'EXT_SOURCE_1', 'EXT_SOURCE_2', 'EXT_SOURCE_3', 'APARTMENTS_AVG', 'BASEMENTAREA_AVG', 'YEARS_BEGINEXPLUATATION_AVG', 'YEARS_BUILD_AVG', 'COMMONAREA_AVG', 'ENTRANCES_AVG', 'FLOORSMAX_AVG', 'FLOORSMIN_AVG', 'LANDAREA_AVG', 'LIVINGAPARTMENTS_AVG', 'NONLIVINGAPARTMENTS_AVG', 'NONLIVINGAREA_AVG', 'OBS_30_CNT_SOCIAL_CIRCLE', 'DEF_30_CNT_SOCIAL_CIRCLE', 'DAYS_LAST_PHONE_CHANGE', 'FLAG_DOCUMENT_2', 'FLAG_DOCUMENT_3', 'FLAG_DOCUMENT_4', 'FLAG_DOCUMENT_5', 'FLAG_DOCUMENT_6', 'FLAG_DOCUMENT_7'

In [49]:
# filtering variables with low correlation
data_train_04 = data_train_04[list_of_variables_to_keep_low_correlation]

In [50]:
# saving pkl
with open(f'{root_path}/{parent_folder_name}/PKL/prd_list_of_variables_to_keep_low_correlation_{parent_folder_name}.pkl', 'wb') as file:
    pickle.dump(list_of_variables_to_keep_low_correlation, file)

## 4.3. Scaler

In [51]:
# scaler
scaler = StandardScaler()

# standardization
data_train_04_scaled = scaler.fit_transform(data_train_04)
data_train_04 = pd.DataFrame(data_train_04_scaled, columns=data_train_04.columns, index=data_train_04.index)

In [52]:
# saving pkl
with open(f'{root_path}/{parent_folder_name}/PKL/prd_scaler_{parent_folder_name}.pkl', 'wb') as file:
    pickle.dump(scaler, file)

# 5. Analytical Base Table (ABT)

In [53]:
# bringing the target to the post dataprep table
abt_train_00 = data_train_04.merge(data_train_01[['TARGET']], left_index=True, right_index=True, how='inner')

# checking
abt_train_00.head()

CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
78719     -0.575932         -1.002571   -0.193670    -0.339207   
2004      -0.575932         -0.338096   -1.071741    -0.716216   
33911      0.792432         -0.790120   -0.082350    -0.349766   
6280      -0.575932          0.113928   -0.818402    -0.940745   
55616     -0.575932         -0.338096   -0.986221    -1.173659   

       REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
78719                   -0.090181   -1.562639       2.127881   
2004                     1.064266   -0.053120      -0.457387   
33911                   -1.132932    0.907441      -0.457719   
6280                     1.064266    0.849295      -0.472233   
55616                   -0.911693    0.796185      -0.458447   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
78719           0.233488        -0.864784     0.000000    0.004212   
2004           -1.083388        -1.129518    -0.297457    0.004212   
33911           0.585390         1.774599     0.000000    0.004212   
6280           -0.282352        -0.817012     0.000000    0.004212   
55616           1.152107        -0.018828    -1.159942    0.004212   

       FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL  \
78719        -0.498237          0.044013   -0.626386   -0.245915   
2004         -0.498237          0.044013   -0.626386   -0.245915   
33911        -0.498237          0.044013   -0.626386   -0.245915   
6280         -0.498237          0.044013   -0.626386   -0.245915   
55616        -0.498237          0.044013   -0.626386   -0.245915   

       OCCUPATION_TYPE  REGION_RATING_CLIENT  HOUR_APPR_PROCESS_START  \
78719         1.118617             -0.100444                 1.204880   
2004         -0.486904             -0.100444                -0.632430   
33911        -1.735642             -0.100444                 0.592444   
6280         -1.200468             -0.100444                 0.286225   
55616        -1.735642             -0.100444                 0.898662   

       REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
78719                   -0.126647                   -0.235314   
2004                    -0.126647                   -0.235314   
33911                   -0.126647                   -0.235314   
6280                    -0.126647                   -0.235314   
55616                   -0.126647                   -0.235314   

       REG_CITY_NOT_LIVE_CITY  REG_CITY_NOT_WORK_CITY  ORGANIZATION_TYPE  \
78719               -0.290985               -0.547304           1.346547   
2004                 3.436607                1.827139          -0.755017   
33911               -0.290985               -0.547304          -1.194879   
6280                -0.290985               -0.547304           1.199926   
55616               -0.290985               -0.547304           0.466822   

       EXT_SOURCE_1  EXT_SOURCE_2  EXT_SOURCE_3  APARTMENTS_AVG  \
78719      1.739545     -0.330462  9.388575e-01    1.833412e-16   
2004       0.000000     -1.950521 -6.373303e-16    1.833412e-16   
33911      0.000000      0.142739 -6.373303e-16   -6.641305e-02   
6280       0.000000      0.678846  1.370500e+00   -2.170199e-01   
55616     -0.469618     -2.140040  1.217635e+00    1.833412e-16   

       BASEMENTAREA_AVG  YEARS_BEGINEXPLUATATION_AVG  YEARS_BUILD_AVG  \
78719      2.624379e-16                 2.554444e-15     1.675501e-15   
2004       2.624379e-16                 2.554444e-15     1.675501e-15   
33911     -4.894380e-01                -1.261743e-01     1.675501e-15   
6280       2.624379e-16                -2.263654e-02     1.675501e-15   
55616      2.624379e-16                 2.554444e-15     1.675501e-15   

       COMMONAREA_AVG  ENTRANCES_AVG  FLOORSMAX_AVG  FLOORSMIN_AVG  \
78719    1.705594e-16   3.943772e-16  -2.695518e-16  -6.027738e-16   
2004     1.705594e-16   3.943772e-16  -2.695518e-16  -6.027738e-16   
33911    1.705594e-16  -1.145358e+00  -9.966669e-01  -6.

In [54]:
# cleaning memory
del data_train_01
del data_train_04

# 6. Applying flow on test

In [55]:
# dropping first variables
data_test_02 = prod_variables_to_drop(data_test_01, list_variables_to_drop)

In [56]:
# dropping nan variables
data_test_03 = prod_variables_to_drop_nan(data_test_02, list_variables_to_drop_nan)

In [57]:
# filling nan values (categorical and numerical)
data_test_04 = prod_variables_to_fill_nan(data_test_03, dict_to_fillna)

In [58]:
# applying label encoder
data_test_04 = prod_label_encoder(data_test_04, dict_to_label_encoder)

In [59]:
# applying one hot encoder
data_test_04 = prod_one_hot_encoder(data_test_04, dict_to_one_hot_encoder)

/home/guilherme/Documents/hackhaton_ds_001_pod_academy/hackhaton_ds_001_pod_academy_env/lib/python3.8/site-packages/sklearn/preprocessing/_encoders.py:228: UserWarning: Found unknown categories in columns [12] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(


In [60]:
# keeping low correlation variables
data_test_04 = prod_correlation(data_test_04, list_of_variables_to_keep_low_correlation)

In [61]:
# applying scaler
data_test_04 = prod_scaler(data_test_04, scaler)

In [62]:
# bringing target
abt_test_00 = data_test_04.merge(data_test_01[['TARGET']], left_index=True, right_index=True, how='inner')

# checking
abt_test_00.head()

CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
55944      0.792432         -0.880524   -0.856441    -0.474918   
48387      0.792432         -0.202488   -0.134598    -0.110020   
1389      -0.575932         -0.112084    1.013729     1.080635   
68844      0.792432          4.634168   -0.930281    -1.096021   
14458     -0.575932         -0.564108   -0.063521    -0.293556   

       REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
55944                   -0.784369    0.379316      -0.480112   
48387                   -0.809389    0.026774      -0.472643   
1389                    -1.143112   -1.391634       2.127881   
68844                   -0.894200    0.395798      -0.490281   
14458                    0.744307   -0.776059      -0.490146   

       DAYS_REGISTRATION  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  \
55944           0.644181        -0.870092     0.000000    0.004212   
48387           0.485331        -0.679669     0.565028    0.004212   
1389           -2.366063        -0.697583     0.000000    0.004212   
68844           0.872281        -1.162693    -1.016195    0.004212   
14458          -1.933040         0.482111     0.000000    0.004212   

       FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL  \
55944        -0.498237          0.044013   -0.626386   -0.245915   
48387        -0.498237          0.044013   -0.626386   -0.245915   
1389         -0.498237          0.044013   -0.626386   -0.245915   
68844        -0.498237          0.044013   -0.626386   -0.245915   
14458        -0.498237          0.044013   -0.626386   -0.245915   

       OCCUPATION_TYPE  REGION_RATING_CLIENT  HOUR_APPR_PROCESS_START  \
55944        -1.378859             -0.100444                -0.632430   
48387        -1.200468             -0.100444                -0.326212   
1389          1.118617              1.849566                -0.326212   
68844        -0.130121             -0.100444                -0.019993   
14458         0.583443             -0.100444                -0.938649   

       REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
55944                   -0.126647                   -0.235314   
48387                   -0.126647                   -0.235314   
1389                    -0.126647                   -0.235314   
68844                   -0.126647                   -0.235314   
14458                   -0.126647                   -0.235314   

       REG_CITY_NOT_LIVE_CITY  REG_CITY_NOT_WORK_CITY  ORGANIZATION_TYPE  \
55944               -0.290985               -0.547304           0.026960   
48387               -0.290985               -0.547304          -1.194879   
1389                -0.290985               -0.547304           1.346547   
68844               -0.290985               -0.547304           0.613443   
14458               -0.290985               -0.547304          -1.194879   

       EXT_SOURCE_1  EXT_SOURCE_2  EXT_SOURCE_3  APARTMENTS_AVG  \
55944      0.000000     -2.307964     -1.415824    8.287268e-02   
48387      0.000000     -0.681086     -0.762793   -1.892765e-01   
1389       0.000000      0.970254      0.587961   -1.487930e+00   
68844      0.000000      0.713441      1.393724   -1.087633e+00   
14458      2.882229      0.593621      1.225925    1.833412e-16   

       BASEMENTAREA_AVG  YEARS_BEGINEXPLUATATION_AVG  YEARS_BUILD_AVG  \
55944      2.624379e-16                 4.099211e-01     2.799112e+00   
48387     -9.886789e-01                 4.099211e-01     2.799112e+00   
1389      -1.593819e+00                 4.408778e-02    -4.848144e-01   
68844     -1.387693e+00                -6.865331e-02    -1.511041e+00   
14458      2.624379e-16                 2.554444e-15     1.675501e-15   

       COMMONAREA_AVG  ENTRANCES_AVG  FLOORSMAX_AVG  FLOORSMIN_AVG  \
55944    1.705594e-16  -6.565705e-01   1.431240e+00   1.994843e+00   
48387    8.547502e-05  -1.635566e+00   1.431240e+00   1.994843e+00   
1389    -1.034741e+00  -1.473584e+00  -2.076600e+00  -1.

# 6. Saving Analytical Base Tables

In [63]:
# saving table abt
abt_train_00.to_csv(f'{root_path}/{parent_folder_name}/DATAS/GOLD/abt_train_00_{parent_folder_name}.csv', index=None)

In [64]:
# saving table abt
abt_test_00.to_csv(f'{root_path}/{parent_folder_name}/DATAS/GOLD/abt_test_00_{parent_folder_name}.csv', index=None)